# CP423: Assignment 1

Group Number: 5

Group Members: Abigail Lee (200469770), Kayleigh Habib (200370580) and Myisha Chaudhry (200591740)

In [ ]:
# MIGHT NEED TO RUN THIS FOR THE NLTK
# pip install certifi

In [1]:
import certifi
import ssl
import os

os.environ["SSL_CERT_FILE"] = certifi.where()

In [2]:
# inputs

import os
import re


import nltk
nltk.download('punkt')
nltk.download("stopwords")
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


## Question 1 : Text Preprocessing
a. Convert all text to lowercase

b. Tokenize the text using NLTK

c. Remove stop words using NLTK

d. Exclude special characters except alphanumeric characters

e. Eliminate singly occurring characters

f. Create a set of all the words

In [3]:
def text_preprocessing(file):

    # reading the file line by line
    lines = file.readlines()

    # a. converting to lowercase
    lines = [x.lower() for x in lines]

    # join all the lines into one string
    data = "".join(lines)

    # b. using the tokenization package to tokenize the words
    tokenization = word_tokenize(data)

    # remove duplicates - less words to do the next steps with
    newtoken = list(dict.fromkeys(tokenization))

    # c. remove any stop words from the NLTK package
    stop_words_lib = set(stopwords.words("english")) # choosing the english stopwords from the package

    # goes through each word, and checks if it is in the library - if it is not then we keep the word, if it is we don't take it
    stop_words = []
    for word in newtoken:
            if word not in stop_words_lib:
                 stop_words.append(word)

    # print(stop_words)

    # d. Remove special characters
    pattern = "[^a-z0-9]" # pattern NOT with any letter between a-z or any number including 0-9 (could also do A-Z but since we already made everything lower don't need to add that)
    alphanumerictxt = []
    # goes through each index in the list and if it matches the pattern it will put an empty string otherwise will preserve the value
    # strips the empty string afterwards
    for i in stop_words:
        alphanumerictxt.append(re.sub(pattern," ", i).strip())

    # e. eliminating any characters of length 1
    updated_list = []

    # goes through each index in the list and if the length is more than 1 will append to new list
    for i in alphanumerictxt:
        if len(i)>1:
            updated_list.append(i)

    # after all the other steps are completed check again to make sure no duplicated values
    final_list = list(dict.fromkeys(updated_list))

    #f
    return final_list


In [4]:
# import data files
# takes the names of the files in the folder and creates a list
file_names = os.listdir("./data")
# file_names

# file id (key)
counter = 1

#dictionary1 - translates the ID which belong to the file
dict_words = {}
# dictionaty2 - file dictionary (id to file name)
dict_files = {}

# goes through each file in the list of file names
for i in file_names:

    # if counter <= 2: #for checking purposes - can remove before submitting

      # gets the working directory (this may be different for everyone)
      file_path = os.getcwd() + "/data/" + i
      # opens the file in reading mode
      file = open(file_path, "r", encoding="utf-8", errors = "ignore" ) # added the encoding and errors as some files had different encoding detectors (note: with new line can add new param --> newline = '/r/n'))
      # calls the function written for question 1 of the assignment
      words = text_preprocessing(file)

      # updates the dictionaries
      dict_words[counter] = words # list of words in this file
      dict_files[counter] = i # list of all the file names

    # increment the counter
      counter+=1

    # closes the file
      file.close()

print(dict_words)
print(dict_files)

{1: ['seven', 'voyages', 'sinbad', 'sailor', 'upon', 'time', 'years', 'ago', 'baghdad', 'lived', 'porter', 'called', 'passing', 'palace', 'one', 'day', 'saw', 'bench', 'great', 'doorway', 'thought', 'would', 'rest', 'put', 'load', 'sit', 'curiosity', 'got', 'better', 'slipping', 'entrance', 'went', 'gardens', 'like', 'heaven', 'everywhere', 'flower', 'beds', 'gushing', 'fountains', 'palm', 'trees', 'whose', 'shade', 'many', 'gentlemen', 'strolling', 'pages', 'served', 'cakes', 'drinks', 'could', 'n t', 'help', 'exclaiming', 'aloud', 'well', 'never', 'worked', 'bone', 'poor', 'always', 'hungry', 'lucky', 'men', 'carry', 'burdens', 'enjoy', 'good', 'food', 'drink', 'yet', 're', 'allah', 'sons', 'world', 'difference', 'people', 'live', 'barely', 'stopped', 'speaking', 'came', 'across', 'said', 'come', 'master', 'wishes', 'speak', 'rather', 'alarmed', 'followed', 'lad', 'hall', 'owner', 'house', 'seated', 'amongst', 'guests', 'name', 'hear', 've', 'complaining', 'know', 'became', 'rich', '

## Question 2 : Inverted Index Implementation
Implement an inverted index data structure for the preprocessed dataset


In [5]:
class HashInvertedIndex:

    #initialize hash table
    def __init__(self, capacity=100):
        self.capacity = capacity
        self.table = [[] for _ in range(capacity)]
        self.count = 0

    #finding the corresponding value for the key
    def _index(self, word):
        index = hash(word) % self.capacity
        return index

    #add key-value pair to the hash table
    def insert(self, key, value):

        #compute the hash index for the word
        hash_index = self._index(key)
        for i, kv in enumerate(self.table[hash_index]):
            k, v = kv
            if k == key:
                #add the value to the existing set of values
                v.add(value)
                #add the entry to the table
                self.table[hash_index][i] = (k,v)
                return
        self.table[hash_index].append((key, {value}))

    #retrieve the set of values for a given key, if not found, returns an empty set
    def retrieve(self, key):
        #compute the hash index for a given key
        hash_index = self._index(key)
        for k, v in self.table[hash_index]:
            #if the key if found, teturn the set
            if k == key:
                return v
        return set()

    #for testing purposes - shows us the string representation of the hash tables
    def __rep__(self):
        return str(self.table)



In [6]:
#build the inverted index
def create_inverted_index():

    inverted_index = HashInvertedIndex()

## Kayleigh's code to evaluate functions

    # import data files
    # takes the names of the files in the folder and creates a list
    file_names = os.listdir("./data")
    # file_names

    # file id (key)
    counter = 1

    #dictionary1 - translates the ID which belong to the file
    dict_words = {}
    # dictionaty2 - file dictionary (id to file name)
    dict_files = {}

    # goes through each file in the list of file names
    for i in file_names:
        # if counter <= 150: #don't need this if statement, just using it so Jupyter doesn't crash from reading all the files

            # gets the working directory (this may be different for everyone)
            file_path = os.getcwd() + "/data/" + i
            # opens the file in reading mode
            file = open(file_path, "r", encoding="utf-8", errors = "ignore" ) # added the encoding and errors as some files had different encoding detectors (note: with new line can add new param --> newline = '/r/n'))
            # calls the function written for question 1 of the assignment
            words = text_preprocessing(file)
            #add the word and file name to the inverted index
            for word in words:
                inverted_index.insert(word, counter) #inserting counter instead of doc name (change later?)


        # increment the counter
            counter+=1

        # closes the file
            file.close()
    return inverted_index

##

In [7]:
inverted_index = create_inverted_index()
print(inverted_index.table)
# print(len(inverted_index))

[[('fountains', {224, 1, 155}), ('every', {1, 4, 5, 6, 7, 8, 9, 10, 11, 14, 16, 18, 19, 21, 24, 25, 26, 28, 30, 32, 33, 34, 35, 36, 37, 43, 44, 45, 48, 53, 57, 58, 59, 62, 63, 64, 65, 66, 67, 69, 73, 75, 76, 77, 79, 80, 82, 83, 84, 89, 91, 92, 93, 97, 101, 102, 103, 104, 105, 106, 108, 109, 110, 112, 113, 119, 123, 124, 125, 128, 131, 133, 134, 136, 137, 138, 139, 140, 142, 145, 146, 149, 150, 152, 153, 154, 155, 156, 159, 161, 163, 164, 166, 167, 171, 173, 174, 179, 181, 183, 187, 188, 197, 198, 200, 201, 204, 205, 206, 208, 210, 213, 214, 215, 216, 219, 220, 221, 222, 224, 228, 229, 231, 232, 239, 242, 245, 247, 248}), ('ask', {1, 3, 4, 5, 6, 7, 8, 9, 11, 14, 21, 26, 28, 32, 33, 35, 44, 47, 48, 53, 59, 62, 63, 66, 67, 68, 70, 71, 73, 75, 76, 77, 78, 79, 80, 83, 89, 92, 93, 97, 98, 102, 104, 105, 106, 108, 109, 112, 123, 124, 126, 133, 143, 144, 149, 152, 153, 154, 155, 158, 164, 166, 168, 169, 170, 174, 179, 181, 187, 190, 191, 194, 196, 197, 198, 200, 201, 202, 203, 210, 211, 215, 2

## Question 3: Query Support
Support the following queries, where x and y would be taken as input from the user

1. x OR y

2. x AND y

3. x AND NOT y

4. x OR NOT y


In [8]:
def _query(query, InvertedIndex):
  new_query = query.strip().split()
  comparisons = 0
  print(new_query)

  for i in range(len(new_query)):
    # index = InvertedIndex._index(item)
    # print(item, (InvertedIndex.retrieve(item)))
    item = new_query[i]
    if len(InvertedIndex.retrieve(item)) != 0 or item in ["AND", "OR", "NOT"]:

      #NOT
      if item == "NOT":
        i += 1
        continue
        #skip not, remove next word's comparisons from total?

      print(item)
      comparisons += len(InvertedIndex.retrieve(item))

  return comparisons



In [91]:
test = _query("lion OR stood OR thoughtfully OR moment", inverted_index)
# test2 = _query("telephone OR NOT paved AND NOT roads", inverted_index)
# test = text_preprocessing("telephone")
print(test)

['lion', 'OR', 'stood', 'OR', 'thoughtfully', 'OR', 'moment']
lion
OR
stood
OR
thoughtfully
OR
moment
241


## Question 4: System Evaluation
Evaluate your system against the set of provided queries.

1. Query #1

- Input Sentence: "lion stood thoughtfully for a moment"

- Input operation sequence: [OR, OR, OR]

- Expected preprocessed query: "lion OR stood OR thoughtfully OR moment"

2. Query #2

- Input Sentence: "telephone, paved, roads"

- Input operation sequence: [OR NOT, AND NOT]

- Expected preprocessed query: "telephone OR NOT paved AND NOT roads


Output should include:
- The number of documents retrieved

- The minimum number of total comparisons made (only for merging the algorithm)

- The list of retrieved document names

In [ ]:
#

In [ ]:
# displaying the required print statements
print("Number of matched documents: ")
print("Minimum number of comparisons required")
print("List of retreived document names: ")
